## Imports


In [10]:
# Provides ways to work with large multidimensional arrays
import numpy as np

# Allows for further data manipulation and analysis
import pandas as pd
import matplotlib.pyplot as plt  # Plotting
import matplotlib.dates as mdates  # Styling dates

import datetime as dt

import time

import yfinance as yf

# Used for file handling like deleting files
# and get data from a directory
import os
from os import listdir
from os.path import isfile, join

import cufflinks as cf
import plotly.express as px
import plotly.graph_objects as go

# Make plotly work in your Jupyter Notebook
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

init_notebook_mode(connected=True)
# Use plotly locally
cf.go_offline()

from plotly.subplots import make_subplots

import warnings

warnings.simplefilter("ignore")


## Constants


In [11]:
# Location of files
PATH = "C:\\Users\\Eduardo Nuñez\\OneDrive\\Programming\\Python\\Derek Banas\\Investing\\AFP\\"
DATA_PATH = PATH + "AFP Data\\"


## Plot with Bollinger Bands


In [12]:
def plot_with_boll_bands(df: pd.DataFrame, fund_name):
    fig = go.Figure()

    value = go.Scatter(x=df.index, y=df[fund_name], line=dict(color="rgba(128,0,30,0.75)", width=2), name="Value")

    upper_line = go.Scatter(x=df.index, y=df["upper_band"], line=dict(color="rgba(250,0,0,0.75)", width=1, dash="dot"), name="Upper Band")

    mid_line = go.Scatter(
        x=df.index,
        y=df["middle_band"],
        line=dict(color="rgba(0,0,250,0.75)", width=0.7, dash="dot"),
        name="Middle Band",
    )

    lower_line = go.Scatter(x=df.index, y=df["lower_band"], line=dict(color="rgba(0,250,0,0.75)", width=1, dash="dot"), name="Lower Band")

    fig.add_trace(value)
    fig.add_trace(upper_line)
    fig.add_trace(mid_line)
    fig.add_trace(lower_line)

    fig.update_xaxes(title="Date", rangeslider_visible=True)
    fig.update_yaxes(title="Price")

    fig.update_layout(title="Fund " + fund_name + " Bollinger Bands", height=800, width=1200, showlegend=True)

    fig.update_layout(
        xaxis=dict(
            rangeselector=dict(
                buttons=list(
                    [
                        dict(count=10, label="10D", step="day", stepmode="backward"),
                        dict(count=1, label="1M", step="month", stepmode="backward"),
                        dict(count=6, label="6M", step="month", stepmode="todate"),
                        dict(count=1, label="YTD", step="year", stepmode="todate"),
                        dict(count=1, label="1Y", step="year", stepmode="backward"),
                        dict(label="All", step="all"),
                    ]
                )
            ),
            rangeslider=dict(visible=True),
            type="date",
        )
    )
    fig.show()


## Plot Ichimoku


In [13]:
def get_fill_color(label):
    if label >= 1:
        return "rgba(0,250,0,0.4)"  # Returns green
    else:
        return "rgba(250,0,0,0.4)"  # Returns red


In [14]:
def plot_ichimoku(df: pd.DataFrame, fund_name):
    # fig = go.Figure()

    value = go.Scatter(x=df.index, y=df[fund_name], line=dict(color="rgba(128,0,30,0.75)", width=2), name="Value")

    df1 = df.copy()
    fig = go.Figure()
    # in this case the fill should be green (value = 1 in get_fill_color)
    df["label"] = np.where(df["SpanA"] > df["SpanB"], 1, 0)
    df["group"] = df["label"].ne(df["label"].shift()).cumsum()
    df = df.groupby("group")

    dfs = []
    for name, data in df:
        dfs.append(data)

    for df in dfs:
        fig.add_traces(go.Scatter(x=df.index, y=df.SpanA, line=dict(color="rgba(0,0,0,0)")))
        fig.add_traces(
            go.Scatter(
                x=df.index,
                y=df.SpanB,
                line=dict(color="rgba(0,0,0,0)"),
                fill="tonexty",
                fillcolor=get_fill_color(df["label"].iloc[0]),
            )
        )

    baseline = go.Scatter(x=df1.index, y=df1["Baseline"], line=dict(color="pink", width=2, dash="dot"), name="Baseline")
    conversion = go.Scatter(x=df1.index, y=df1["Conversion"], line=dict(color="black", width=1, dash="dot"), name="Conversion")
    lagging = go.Scatter(x=df1.index, y=df1["Lagging"], line=dict(color="purple", width=2, dash="dot"), name="Lagging")
    span_a = go.Scatter(x=df1.index, y=df1["SpanA"], line=dict(color="green", width=2, dash="dot"), name="Span A")
    span_b = go.Scatter(x=df1.index, y=df1["SpanB"], line=dict(color="red", width=1, dash="dot"), name="Span B")

    fig.add_trace(value)
    fig.add_trace(baseline)
    fig.add_trace(conversion)
    fig.add_trace(lagging)
    fig.add_trace(span_a)
    fig.add_trace(span_b)

    fig.update_xaxes(title="Date", rangeslider_visible=True)
    fig.update_yaxes(title="Price")

    fig.update_layout(title="Fund " + fund_name + " Ichimoku", height=800, width=1200, showlegend=True)

    fig.update_layout(
        xaxis=dict(
            rangeselector=dict(
                buttons=list(
                    [
                        dict(count=10, label="10D", step="day", stepmode="backward"),
                        dict(count=1, label="1M", step="month", stepmode="backward"),
                        dict(count=6, label="6M", step="month", stepmode="todate"),
                        dict(count=1, label="YTD", step="year", stepmode="todate"),
                        dict(count=1, label="1Y", step="year", stepmode="backward"),
                        dict(label="All", step="all"),
                    ]
                )
            ),
            rangeslider=dict(visible=True),
            type="date",
        )
    )

    fig.show()


## Plot MACD


In [15]:
def plot_MACD(df: pd.DataFrame, fund_name):
    fig = go.Figure()

    value = go.Scatter(x=df.index, y=df["MACD"], line=dict(color="rgba(0,0,0,0.75)", width=1), name="Value")

    fig.add_trace(value)

    fig.update_xaxes(title="Date", rangeslider_visible=True)
    fig.update_yaxes(title="MACD")

    fig.update_layout(title="Fund " + fund_name + " MACD", height=800, width=1200, showlegend=True)
    fig.show()


In [16]:
def get_fund_df_from_csv(fund_name):
    try:
        fund_df = pd.read_csv(DATA_PATH + fund_name + ".csv", index_col=0)
    except FileNotFoundError:
        print("File doesn't exist")
    else:
        return fund_df


In [17]:
funds = ["A", "B", "C", "D", "E"]
fund_df_list = []
for fund in funds:
    fund_df_list.append(get_fund_df_from_csv(fund))

# fund_df_list


In [18]:
for fund_df in fund_df_list:
    fund_name = fund_df.columns[0]
    plot_with_boll_bands(fund_df, fund_name)
    plot_ichimoku(fund_df, fund_name)
    plot_MACD(fund_df, fund_name)
